In [2]:
from datasets import Audio, Dataset, load_dataset, load_metric
from transformers import AutoFeatureExtractor, pipeline

language_code = "ja"
dataset_name = "mozilla-foundation/common_voice_8_0"

common_voice_train = load_dataset(dataset_name, language_code, use_auth_token=True, split="train+validation")
common_voice_test = load_dataset(dataset_name, language_code, use_auth_token=True, split="test")


print(len(common_voice_train))

# # for testing: only process the first two examples as a test
# dataset = dataset.select(range(10))




Downloading:   0%|          | 0.00/10.1k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.98k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/53.1k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/958M [00:00<?, ?B/s]

0 examples [00:00, ? examples/s]

...

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

Dataset common_voice downloaded and prepared to /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/ja/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8. Subsequent calls will reuse this data.


Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/ja/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)


10623


In [1]:
!pip install pykakasi

     |████████████████████████████████| 2.4 MB 9.9 MB/s            
  Preparing metadata (setup.py) ... done
     |████████████████████████████████| 84 kB 12.8 MB/s            
  Created wheel for jaconv: filename=jaconv-0.3-py3-none-any.whl size=15553 sha256=fd764f215e4d567cb60062a7052497b66729e9e2190e2e00153e0d19734088e7
  Stored in directory: /workspace/.cache/pip/wheels/73/e8/fb/b4ad8117719f79ac73bc05406d1768f845688cdbeed7aad87e
Successfully built jaconv
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [4]:
from pykakasi import kakasi

kakasi = kakasi()
kakasi.setMode('J', 'H') #Convert from kanji to hiragana
# kakasi.setMode("K", "H") #Convert from katakana to hiragana
conv = kakasi.getConverter()

str = 'にんじゃ 平仮名 kana'

print(conv.do(str))

にんじゃ ひらがな kana


/tmp/ipykernel_2159/3076271513.py:4: DeprecationWarning: Call to deprecated method setMode. (Old API will be removed in v3.0.) -- Deprecated since version 2.1.
  kakasi.setMode('J', 'H') #Convert from kanji to hiragana
/tmp/ipykernel_2159/3076271513.py:6: DeprecationWarning: Call to deprecated method getConverter. (Old API will be removed in v3.0.) -- Deprecated since version 2.1.
  conv = kakasi.getConverter()
/tmp/ipykernel_2159/3076271513.py:10: DeprecationWarning: Call to deprecated method do. (Old API will be removed in v3.0.) -- Deprecated since version 2.1.
  print(conv.do(str))


In [3]:
repo_name = 'https://huggingface.co/AndrewMcDowell/wav2vec2-xls-r-1B-german'


In [4]:
common_voice_train = common_voice_train.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])
common_voice_test = common_voice_test.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])



In [15]:
import re
chars_to_remove_regex = '[\,\?\!\-\;\:\"\“\%\‘\”\�\—\’\…\–\（\，\[\]\)\(\！]'
# \.
def remove_special_characters(batch):
    batch["sentence"] = conv.do(re.sub(chars_to_remove_regex, '', batch["sentence"]))
    return batch

common_voice_train = common_voice_train.map(remove_special_characters)
common_voice_test = common_voice_test.map(remove_special_characters)

0ex [00:00, ?ex/s]

/tmp/ipykernel_2159/322450745.py:5: DeprecationWarning: Call to deprecated method do. (Old API will be removed in v3.0.) -- Deprecated since version 2.1.
  batch["sentence"] = conv.do(re.sub(chars_to_remove_regex, '', batch["sentence"]))


0ex [00:00, ?ex/s]

In [24]:
common_voice_train[1]

{'client_id': '02a8841a00d762472a4797b56ee01643e8d9ece5a225f2e91c007ab1f94c49c99e50d19986ff3fefb18190257323f34238828114aa607f84fbe9764ecf5aaeaa',
 'path': 'cv-corpus-8.0-2022-01-19/ja/clips/common_voice_ja_25467658.mp3',
 'audio': {'path': 'cv-corpus-8.0-2022-01-19/ja/clips/common_voice_ja_25467658.mp3',
  'array': array([0.        , 0.        , 0.        , ..., 0.00026336, 0.00038834,
         0.00026771], dtype=float32),
  'sampling_rate': 48000},
 'sentence': 'ちょっとがっこうでトラブルがありまして。',
 'up_votes': 2,
 'down_votes': 0,
 'age': 'fourties',
 'gender': 'female',
 'accent': '',
 'locale': 'ja',
 'segment': ''}

In [25]:
!pip install --upgrade datasets

     |████████████████████████████████| 311 kB 11.0 MB/s            
  Attempting uninstall: datasets
    Found existing installation: datasets 1.18.2.dev0
    Uninstalling datasets-1.18.2.dev0:
ERROR: Could not install packages due to an OSError: [Errno 13] Permission denied: 'entry_points.txt'
Consider using the `--user` option or check the permissions.

You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [6]:
!pip install num2words

     |████████████████████████████████| 101 kB 7.9 MB/s            
  Preparing metadata (setup.py) ... done
  Created wheel for docopt: filename=docopt-0.6.2-py2.py3-none-any.whl size=13704 sha256=7cda85e4b3980668714aad8f5d706fb5b189c2804ce1d99ca2380537fdc78031
  Stored in directory: /workspace/.cache/pip/wheels/56/ea/58/ead137b087d9e326852a851351d1debf4ada529b6ac0ec4e8c
Successfully built docopt
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [7]:

from num2words import num2words
import regex as re
matches = []

def replace_numbers(match):
    match = match.group()
    matches.append(match)
    return num2words(match, lang='de')

def replace_numbers_in_batch(batch):
    batch["sentence"] = re.sub(r'\d+(?:,\d+)?', replace_numbers, batch["sentence"])
    return batch

common_voice_test_2 = common_voice_test.map(replace_numbers_in_batch)

0ex [00:00, ?ex/s]

In [10]:
common_voice_train_2 = common_voice_train.map(replace_numbers_in_batch)

0ex [00:00, ?ex/s]

In [11]:
len(matches)

0

In [ ]:
# def replace_accented_characters(batch):
#     accented_string = u'Málaga'
#     # accented_string is of type 'unicode'
#     import unidecode
#     unaccented_string = unidecode.unidecode(accented_string)
#     batch["sentence"] = re.sub('[â]', 'a', batch["sentence"])
#     batch["sentence"] = re.sub('[î]', 'i', batch["sentence"])
#     batch["sentence"] = re.sub('[ô]', 'o', batch["sentence"])
#     batch["sentence"] = re.sub('[û]', 'u', batch["sentence"])
#     return batch

def strip_accents(batch):
    return ''.join(c for c in unicodedata.normalize('NFD', batch["sentence"]) if unicodedata.category(c) != 'Mn')

common_voice_train = common_voice_train.map(replace_accented_characters)
common_voice_test = common_voice_test.map(replace_accented_characters)

In [6]:
def extract_all_chars(batch):
    all_text = " ".join(batch["sentence"])
    vocab = list(set(all_text))
    return {"vocab": [vocab], "all_text": [all_text]}

In [16]:
vocab_train = common_voice_train.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_train.column_names)
vocab_test = common_voice_test.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_test.column_names)

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

In [17]:
vocab_list = list(set(vocab_train["vocab"][0]) | set(vocab_test["vocab"][0]))

In [19]:
# vocab_train["vocab"]

[['ん',
  'ン',
  'ダ',
  'S',
  'う',
  'た',
  'ぽ',
  'P',
  '：',
  '々',
  'か',
  'ぞ',
  'よ',
  'や',
  'ヨ',
  'ゃ',
  'Q',
  'N',
  'だ',
  'を',
  'L',
  'ｈ',
  'Ｆ',
  'E',
  'ピ',
  'ち',
  'ボ',
  'w',
  'リ',
  'ゲ',
  'フ',
  'あ',
  'ウ',
  'め',
  'タ',
  'ぬ',
  'せ',
  'て',
  'b',
  '」',
  'す',
  'び',
  'ば',
  'ア',
  'A',
  'r',
  'ャ',
  'イ',
  'へ',
  'ぶ',
  'は',
  'u',
  'と',
  '繫',
  'ぎ',
  'バ',
  'ノ',
  'I',
  'ざ',
  'R',
  'チ',
  'Ａ',
  '｢',
  'G',
  'ェ',
  'く',
  'け',
  'ぇ',
  '？',
  '〜',
  'つ',
  'わ',
  'こ',
  'ス',
  'ズ',
  'p',
  'y',
  'ぼ',
  'し',
  '、',
  '！',
  'ゼ',
  's',
  'Ｕ',
  'き',
  'ゥ',
  '・',
  'が',
  'も',
  'エ',
  'ク',
  'づ',
  'O',
  'グ',
  'ブ',
  'ゅ',
  'ィ',
  'ぁ',
  'd',
  't',
  'ｊ',
  'n',
  'ロ',
  'g',
  'ー',
  '/',
  'ナ',
  'ヅ',
  'の',
  'ケ',
  'ほ',
  '･',
  '）',
  'J',
  'D',
  'ネ',
  'お',
  'パ',
  'ム',
  'む',
  'ラ',
  'ミ',
  'い',
  'ろ',
  'c',
  '＝',
  'z',
  'ベ',
  'Ｏ',
  'h',
  'プ',
  'o',
  'ザ',
  '&',
  '『',
  'ソ',
  '.',
  'ヴ',
  'l',
  'ド',
  'み',
  'v',
  'x',

In [18]:
print(len(vocab_list))
print(vocab_list)

249
['ダ', 'た', 'P', 'か', 'よ', 'や', 'Q', 'を', 'Ｆ', 'ｈ', 'E', 'ち', 'リ', 'ゲ', 'フ', 'め', 'タ', 'せ', 'b', '」', 'ば', 'ア', 'A', 'ャ', 'イ', 'ぶ', 'は', 'u', 'と', 'ノ', 'I', 'R', '｢', 'G', 'ェ', 'く', '？', '〜', 'つ', 'こ', 'Ｓ', 'ぼ', 'ゼ', 's', 'Ｕ', 'き', 'ゥ', 'が', 'も', 'エ', 'ク', 'づ', 'グ', 'ブ', 'ゅ', 'ィ', 't', 'n', 'ロ', 'ー', '/', 'の', 'ケ', '･', 'J', 'お', 'む', 'Ｐ', 'ベ', 'h', 'プ', 'o', '&', '『', 'ソ', '.', 'ヴ', 'ド', 'み', 'Y', 'ガ', 'ょ', 'カ', 'C', 'ぜ', 'j', '．', 'ご', 'ど', 'ハ', 'ね', 'W', 'ｊ', 'T', ' ', 'マ', '―', '－', 'デ', 'ゾ', 'ポ', 'K', 'ペ', 'ぱ', 'ふ', 'べ', 'ヒ', 'e', 'サ', 'Ｎ', 'X', 'ュ', 'k', 'り', 'U', 'ひ', 'げ', 'ゆ', 'ず', 'ゴ', 'a', 'ョ', 'ツ', '〇', 'え', 'F', 'B', '』', 'ッ', 'ん', 'ン', 'S', 'う', 'ぽ', '：', '々', 'ぞ', 'N', 'ヨ', 'ゃ', 'だ', 'L', 'ピ', 'ボ', 'w', 'ウ', 'あ', 'ヶ', 'ぬ', 'て', 'す', 'び', 'r', 'へ', '繫', 'バ', 'ぎ', 'ざ', 'Ａ', 'チ', 'け', 'ぇ', 'わ', 'ス', 'p', 'ズ', 'y', 'し', '、', '！', 'Ｇ', '・', 'O', 'ぁ', 'd', 'g', 'ナ', 'ヅ', 'ほ', '）', 'D', 'ネ', 'パ', 'ム', 'ミ', '＝', 'z', 'い', 'ろ', 'c', 'Ｏ', 'ザ', 'l', 'v', 'x', 'ヌ', 'に', 'ら', 'ヘ', 

In [26]:
j_vocab = {"<pad>": 0, "<s>": 1, "</s>": 2, "<unk>": 3, "|": 4, "'": 5, "-": 6, "A": 7, "B": 8, "C": 9, "D": 10, "E": 11, "F": 12, "G": 13, "H": 14, "I": 15, "J": 16, "K": 17, "L": 18, "M": 19, "N": 20, "O": 21, "P": 22, "Q": 23, "R": 24, "S": 25, "T": 26, "U": 27, "V": 28, "W": 29, "X": 30, "Y": 31, "Z": 32, "Ä": 33, "Í": 34, "Ó": 35, "Ö": 36, "Ü": 37}


In [48]:
manually_kept_values = ['ß', 'ä', 'ö', 'ü']

punctuation = ['.', ]

In [50]:
odd_values = []
for index, value in enumerate(sorted(vocab_list)):
#     if :
    if value not in j_vocab and not (16 <= index <= 41 or value == ' ') and value not in manually_kept_values:
        odd_values.append(value)
#     print(index, value)
    
print(odd_values)

['$', '&', '(', ')', '*', '+', '.', '/', '=', '@', '[', ']', '_', '`', '¡', '§', '«', '°', '´', 'µ', '·', '»', '×', 'à', 'á', 'â', 'ã', 'å', 'æ', 'ç', 'è', 'é', 'ê', 'ë', 'ì', 'í', 'î', 'ï', 'ð', 'ñ', 'ò', 'ó', 'ô', 'õ', 'ø', 'ù', 'ú', 'û', 'ý', 'þ', 'ā', 'ă', 'ą', 'ć', 'č', 'ď', 'đ', 'ē', 'ė', 'ę', 'ě', 'ğ', 'ġ', 'ħ', 'ī', 'ı', 'ł', 'ń', 'ņ', 'ň', 'ō', 'ŏ', 'ő', 'œ', 'ř', 'ś', 'ş', 'š', 'ť', 'ū', 'ů', 'ź', 'ż', 'ž', 'ơ', 'ǐ', 'ǔ', 'ș', 'ț', 'ə', 'ʻ', 'ʾ', 'ʿ', '̆', '̇', '̥', 'а', 'в', 'е', 'и', 'к', 'м', 'о', 'р', 'с', 'ф', 'ч', 'ш', 'ѹ', 'א', 'ב', 'נ', 'ע', 'ש', '་', 'ན', 'ḫ', 'ṟ', 'ṣ', 'ṭ', 'ạ', 'ả', 'ắ', 'ằ', 'ế', 'ễ', 'ệ', 'ọ', 'ồ', 'ộ', 'ụ', 'ứ', '‑', '‚', '„', '‟', '′', '″', '‹', '›', '→', '−', '≡', '⟨', '⟩', 'カ', '东', '临', '乡', '关', '合', '城', '孙', '尣', '幺', '支', '比', '毛', '泽', '無', '生', '臣', '辶', '道', '镇', '黃']


In [63]:
print(" ".join(odd_values))

# for value in odd_values:
#     if value not in manually_kept_values:
#         print(value)

$ & ( ) * + . / = @ [ ] _ ` ¡ § « ° ´ µ · » × à á â ã å æ ç è é ê ë ì í î ï ð ñ ò ó ô õ ø ù ú û ý þ ā ă ą ć č ď đ ē ė ę ě ğ ġ ħ ī ı ł ń ņ ň ō ŏ ő œ ř ś ş š ť ū ů ź ż ž ơ ǐ ǔ ș ț ə ʻ ʾ ʿ ̆ ̇ ̥ а в е и к м о р с ф ч ш ѹ א ב נ ע ש ་ ན ḫ ṟ ṣ ṭ ạ ả ắ ằ ế ễ ệ ọ ồ ộ ụ ứ ‑ ‚ „ ‟ ′ ″ ‹ › → − ≡ ⟨ ⟩ カ 东 临 乡 关 合 城 孙 尣 幺 支 比 毛 泽 無 生 臣 辶 道 镇 黃


In [ ]:
$ & ( ) * + = @ [ ] _ ` ¡ § « ° ´ µ · » × à á â ã å æ ç è é ê ë ì í î ï ð ñ ò ó ô õ ø ù ú û ý þ ā ă ą ć č ď đ ē ė ę ě ğ ġ ħ ī ı ł ń ņ ň ō ŏ ő œ ř ś ş š ť ū ů ź ż ž ơ ǐ ǔ ș ț ə ʻ ʾ ʿ ̆ ̇ ̥ а в е и к м о р с ф ч ш ѹ א ב נ ע ש ་ ན ḫ ṟ ṣ ṭ ạ ả ắ ằ ế ễ ệ ọ ồ ộ ụ ứ ‑ ‚ „ ‟ ′ ″ ‹ › → − ≡ ⟨ ⟩ カ 东 临 乡 关 合 城 孙 尣 幺 支 比 毛 泽 無 生 臣 辶 道 镇 黃

In [54]:
filtered_vocab_list = [value for value in vocab_list if value not in odd_values]

In [55]:
filtered_vocab_list

['ß',
 'j',
 'r',
 'h',
 'd',
 'l',
 'z',
 'n',
 'm',
 'c',
 'ä',
 "'",
 'g',
 'e',
 'w',
 's',
 'u',
 'k',
 'o',
 'f',
 ' ',
 'y',
 'v',
 'ö',
 'ü',
 'p',
 'a',
 'x',
 'b',
 'q',
 't',
 'i']

In [21]:
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}

# replace white space with delimiter token
if word_delimiter_token is not None:
    vocab_dict[word_delimiter_token] = vocab_dict[" "]
    del vocab_dict[" "]

# add unk and pad token
if unk_token is not None:
    vocab_dict[unk_token] = len(vocab_dict)

if pad_token is not None:
    vocab_dict[pad_token] = len(vocab_dict)

NameError: name 'word_delimiter_token' is not defined

In [58]:
vocab_set = set(filtered_vocab_list)
train_dataset_size = len(common_voice_train)
common_voice_train_2 = common_voice_train.filter(
    lambda example: vocab_set.issuperset(example["sentence"].replace(" ", ""))
)
print(f"OOV found in {train_dataset_size - len(common_voice_train_2)} samples, and they were removed from training set")
print(f"The final training set size is {len(common_voice_train_2)}")

  0%|          | 0/437 [00:00<?, ?ba/s]

OOV found in 421223 samples, and they were removed from training set
The final training set size is 14947


KeyboardInterrupt: 

0

In [22]:
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}
for key, value in enumerate(vocab_dict):
    print(key, value)

0  
1 &
2 '
3 .
4 /
5 A
6 B
7 C
8 D
9 E
10 F
11 G
12 H
13 I
14 J
15 K
16 L
17 M
18 N
19 O
20 P
21 Q
22 R
23 S
24 T
25 U
26 V
27 W
28 X
29 Y
30 Z
31 a
32 b
33 c
34 d
35 e
36 f
37 g
38 h
39 i
40 j
41 k
42 l
43 m
44 n
45 o
46 p
47 q
48 r
49 s
50 t
51 u
52 v
53 w
54 x
55 y
56 z
57 ―
58 、
59 。
60 々
61 〇
62 「
63 」
64 『
65 』
66 〜
67 ぁ
68 あ
69 い
70 う
71 ぇ
72 え
73 お
74 か
75 が
76 き
77 ぎ
78 く
79 ぐ
80 け
81 げ
82 こ
83 ご
84 さ
85 ざ
86 し
87 じ
88 す
89 ず
90 せ
91 ぜ
92 そ
93 ぞ
94 た
95 だ
96 ち
97 ぢ
98 っ
99 つ
100 づ
101 て
102 で
103 と
104 ど
105 な
106 に
107 ぬ
108 ね
109 の
110 は
111 ば
112 ぱ
113 ひ
114 び
115 ぴ
116 ふ
117 ぶ
118 ぷ
119 へ
120 べ
121 ぺ
122 ほ
123 ぼ
124 ぽ
125 ま
126 み
127 む
128 め
129 も
130 ゃ
131 や
132 ゅ
133 ゆ
134 ょ
135 よ
136 ら
137 り
138 る
139 れ
140 ろ
141 わ
142 を
143 ん
144 ァ
145 ア
146 ィ
147 イ
148 ゥ
149 ウ
150 ェ
151 エ
152 ォ
153 オ
154 カ
155 ガ
156 キ
157 ギ
158 ク
159 グ
160 ケ
161 ゲ
162 コ
163 ゴ
164 サ
165 ザ
166 シ
167 ジ
168 ス
169 ズ
170 セ
171 ゼ
172 ソ
173 ゾ
174 タ
175 ダ
176 チ
177 ッ
178 ツ
179 ヅ
180 テ
181 デ
182 ト
183 ド
184 ナ


In [ ]:
def create_vocabulary_from_data(
    datasets: DatasetDict,
    word_delimiter_token: Optional[str] = None,
    unk_token: Optional[str] = None,
    pad_token: Optional[str] = None,
):
    # Given training and test labels create vocabulary
    def extract_all_chars(batch):
        all_text = " ".join(batch["target_text"])
        vocab = list(set(all_text))
        return {"vocab": [vocab], "all_text": [all_text]}

    vocabs = datasets.map(
        extract_all_chars,
        batched=True,
        batch_size=-1,
        keep_in_memory=True,
        remove_columns=datasets["train"].column_names,
    )

    # take union of all unique characters in each dataset
    vocab_set = functools.reduce(
        lambda vocab_1, vocab_2: set(vocab_1["vocab"][0]) | set(vocab_2["vocab"][0]), vocabs.values()
    )

    vocab_dict = {v: k for k, v in enumerate(sorted(list(vocab_set)))}

    # replace white space with delimiter token
    if word_delimiter_token is not None:
        vocab_dict[word_delimiter_token] = vocab_dict[" "]
        del vocab_dict[" "]

    # add unk and pad token
    if unk_token is not None:
        vocab_dict[unk_token] = len(vocab_dict)

    if pad_token is not None:
        vocab_dict[pad_token] = len(vocab_dict)

    return vocab_dict

In [ ]:
# load processor
feature_extractor = AutoFeatureExtractor.from_pretrained(repo_name)
# feature_extractor = processor_with_lm.feature_extractor
sampling_rate = feature_extractor.sampling_rate

# resample audio
dataset = dataset.cast_column("audio", Audio(sampling_rate=sampling_rate))

# load eval pipeline
asr = pipeline("automatic-speech-recognition", model=repo_name, feature_extractor=feature_extractor)

# map function to decode audio
def map_to_pred(batch):
    prediction = asr(
        batch["audio"]["array"])

    batch["prediction"] = prediction["text"]
    batch["target"] = batch["sentence"]
    return batch

# run inference on all examples
result = dataset.map(map_to_pred, remove_columns=dataset.column_names)
print(result["prediction"])

result[0]['target']